This notebook can be executed on either cpu or gpu runtime.

To run on gpu, change the
```
.to('cpu')
```
to

```
.to('gpu')
```

In [1]:
# Download nessecary libraries
!pip install datasets==2.10.0 --quiet
!pip install transformers --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 kB 4.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 11.8 MB/s eta 0:00:00


In [2]:
from google.colab import drive
drive.mount('/content/drive/')
root_dir = "./drive/MyDrive/ASR_Colab/" #change it to your own path

Mounted at /content/drive/


In [3]:
# Load the preprocessed dataet
from datasets import load_from_disk
from os import path
import numpy as np

ds_test = load_from_disk(path.join(root_dir , "dataset/test"))

In [4]:
from transformers import  Wav2Vec2CTCTokenizer ,Wav2Vec2FeatureExtractor,Wav2Vec2Processor

tokenizer = Wav2Vec2CTCTokenizer(path.join(root_dir ,"vocab.json"), unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [5]:
# Load the model weights
from transformers import Wav2Vec2ForCTC
model = Wav2Vec2ForCTC.from_pretrained(path.join(root_dir ,"model_weights")).to("cpu")

In [6]:
# select 20 random samples from the test dataset
selected_samples = np.random.randint(low = 0 , high= len(ds_test) , size=20)

In [7]:
import torch

# Initialize empty lists to store predicted outputs and other columns
predicted = []
real_sentences = []
audios = []
gender = []
accent = []
tone = []


# Iterate through the selected samples in the test dataset
for sample in ds_test.select(selected_samples):
  model_input = processor(sample["input_values"], return_tensors="pt", padding=True,sampling_rate=16000)

  # Move the input values to GPU and obtain model predictions
  logits = model(model_input.input_values.to("cpu")).logits
  pred_ids = torch.argmax(logits, dim=-1)[0]

  # Append the predicted output, real sentence labels, and audio inputs and other columns to their respective lists
  predicted.append(pred_ids)
  real_sentences.append(sample["transcript"])
  audios.append(sample["input_values"])
  gender.append(sample["gender"])
  accent.append(sample["accent"])
  tone.append(sample["tone"])

In [8]:
import IPython.display as ipd

dashed = "_-_-"*100

for id_sample in range(len(predicted)):
  # Display the predicted text generated by the model
  print("Prediction:")
  print(processor.decode(predicted[id_sample]))

  # Display the reference (real) text
  print("\nReference:")
  print(real_sentences[id_sample])

  # Display the audio
  print("\nAudio:")
  speech = audios[id_sample]

  # Display the audio using IPython Audio with autoplay enabled
  ipd.display(ipd.Audio(data=speech, rate=16000))

  print(f'gender: {gender[id_sample]}, accent: {accent[id_sample]}, tone: {tone[id_sample]}')
  print(dashed)

Prediction:
ایا میتوانم به دربان ب گویام که اگر ساهب خوان خوان است مای به ملاقات ایشان هستم

Reference:
ایا می توانم به دربان بگویم که اگر صاحب خانه خانه است مایل به ملاقات ایشان هستم 

Audio:


gender: male, accent: فارسی, tone: question
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
تا دساورد مقیت های خواس به هدگ سر

Reference:
تا دستاورد موقعیتهای خاص به حداکثر 

Audio:


gender: male, accent: فارسی, tone: incomplete 
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
این کتام هاسل سالهای کسادی اخیر و سالها زندگی بیبرکت است

Reference:
این کتاب حاصل سال های کسادی اخیر و سال ها زندگی بی برکت است 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
قسمت فیزیکی شامل ورزش هش سات خوابیدن در شوان روز خوردن قزای خوب بول موق نکشیدن سیگار و همه چیز های است کمه می دانند

Reference:
قسمت فیزیکی شامل ورزش هشت ساعت خوابیدن در شبانه روز خوردن غذای خوب و به موقع نکشیدن سیگار و همه چیزهایی است که همه می دانند 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
تروا و پریا یک نفر بودند

Reference:
پروا و پریا یک نفر بودند 

Audio:


...

gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
ببینید که زندگی چقل می تواند بام ازو جالب باشد وای ببینیند که اقما چق میتوانت شادیا فریم برا یک انسان قمگیم باشد

Reference:
ببینید که زندگی چقدر میتواند بامزه و جالب باشد وای ببینید که اغما چقدر میتواند شادی افرین برای یک انسان غمگین باشد 

Audio:


gender: male, accent: فارسی, tone: exclamatory
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
و این جوری شا توشیش سال دور کار زریف نقاشی را قلم گرفتم

Reference:
 و این جوری شد که تو شش سالگی دور کار ظریف نقاشی را قلم گرفتم 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
انواچ ب تور ریتمیک به ساهل بر خورد میکنند

Reference:
امواج به طور ریتمیک به ساحل برخورد می کنند 

Audio:


gender: female, accent: فارسی , tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
سدی نخستین  شار ایرانی است که اسارش بهیکی از زبان های اوروپای ترجمهشده است

Reference:
سعدی نخستین شاعر ایرانی است که اثارش به یکی از زبان های اروپایی ترجمه شده است 

Audio:


gender: female, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
